# Whats the Cause of your Power Outage?

**Name(s)**: Kaii Bijlani, Ketan Mittal

**Website Link**: https://k1mittal.github.io/Causes_of_Power_Outages/

In [2]:
import pandas as pd
import numpy as np
from pathlib import Path
import scipy

import plotly.express as px
pd.options.plotting.backend = 'plotly'

from dsc80_utils import * # Feel free to uncomment and use this.

## Step 1: Introduction

### Interesting Questions:
- How does the cause of the power outages indicate other factors, for example, does whether related power outages result in more people having no power? Can we predict the cause of power outages?
- Is there a correlation between the time and other factors, do power outages happen in one month specifically? Has the number of power outages decreased over time? Can we predict when the next power outage is using a time series prediction?
- Can we predict the number of people affected by a power outage given certain factors? Are the number of people affected by power outages correlated to other factors?
- Can we predict the duration of power outages given certain factors? How are the duration of power outages correlated to other factors?

### Our Choice:
We decided to answer the first bullet point, which is what aspects of power outage are related to each category of cause. 

## Step 2: Data Cleaning and Exploratory Data Analysis

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
# Data Init and Cleaning
raw_data = pd.read_excel(Path('.\outage.xlsx'))
raw_data.columns = [f'{raw_data.columns[i]}_{raw_data.iloc[0].fillna("")[i]}' for i in range(len(raw_data.columns))]
raw_data = raw_data.iloc[1:, 1:]
raw_data.head()

<>:2: SyntaxWarning:

invalid escape sequence '\o'

<>:2: SyntaxWarning:

invalid escape sequence '\o'

C:\Users\Kaii Bijlani\AppData\Local\Temp\ipykernel_26476\3157842531.py:2: SyntaxWarning:

invalid escape sequence '\o'

C:\Users\Kaii Bijlani\AppData\Local\Temp\ipykernel_26476\3157842531.py:3: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`



OBS_   YEAR_  MONTH_ U.S._STATE_ POSTAL.CODE_ NERC.REGION_  \
1   1.0  2011.0     7.0   Minnesota           MN          MRO   
2   2.0  2014.0     5.0   Minnesota           MN          MRO   
3   3.0  2010.0    10.0   Minnesota           MN          MRO   
4   4.0  2012.0     6.0   Minnesota           MN          MRO   
5   5.0  2015.0     7.0   Minnesota           MN          MRO   

      CLIMATE.REGION_ ANOMALY.LEVEL_numeric CLIMATE.CATEGORY_  \
1  East North Central                  -0.3            normal   
2  East North Central                  -0.1            normal   
3  East North Central                  -1.5              cold   
4  East North Central                  -0.1            normal   
5  East North Central                   1.2              warm   

  OUTAGE.START.DATE_Day of the week, Month Day, Year  \
1                                2011-07-01 00:00:00   
2                                2014-05-11 00:00:00   
3                                2010-10-26 00:00:00   
4                                2012-06-19 00:00:00   
5                                2015-07-18 00:00:00   

  OUTAGE.START.TIME_Hour:Minute:Second (AM / PM)  \
1                                       17:00:00   
2                                       18:38:00   
3                                       20:00:00   
4                                       04:30:00   
5                                       02:00:00   

  OUTAGE.RESTORATION.DATE_Day of the week, Month Day, Year  \
1                                2011-07-03 00:00:00         
2                                2014-05-11 00:00:00         
3                                2010-10-28 00:00:00         
4                                2012-06-20 00:00:00         
5                                2015-07-19 00:00:00         

  OUTAGE.RESTORATION.TIME_Hour:Minute:Second (AM / PM)     CAUSE.CATEGORY_  \
1                                           20:00:00        severe weather   
2                                           18:39:00    intentional attack   
3                                           22:00:00        severe weather   
4                                           23:00:00        severe weather   
5                                           07:00:00        severe weather   

  CAUSE.CATEGORY.DETAIL_ HURRICANE.NAMES_ OUTAGE.DURATION_mins  \
1                    NaN              NaN                 3060   
2              vandalism              NaN                    1   
3             heavy wind              NaN                 3000   
4           thunderstorm              NaN                 2550   
5                    NaN              NaN                 1740   

  DEMAND.LOSS.MW_Megawatt  CUSTOMERS.AFFECTED_  \
1                     NaN              70000.0   
2                     NaN                  NaN   
3                     NaN              70000.0   
4                     NaN              68200.0   
5                     250             250000.0   

  RES.PRICE_cents / kilowatt-hour COM.PRICE_cents / kilowatt-hour  \
1                            11.6                            9.18   
2                           12.12                            9.71   
3                           10.87                            8.19   
4                           11.79                            9.25   
5                           13.07                           10.16   

  IND.PRICE_cents / kilowatt-hour TOTAL.PRICE_cents / kilowatt-hour  \
1                            6.81                              9.28   
2                            6.49                              9.28   
3                            6.07                              8.15   
4                            6.71                              9.19   
5                            7.74                             10.43   

  RES.SALES_Megawatt-hour COM.SALES_Megawatt-hour IND.SALES_Megawatt-hour  \
1                 2332915                 2114774                 2113291   
2                 1586986          

In [5]:
fig2 = px.histogram(raw_data, x = 'CAUSE.CATEGORY_', title = 'Distributions of Observations by Cause', histnorm = 'probability density')
fig2.update_layout(xaxis_title = 'Cause', yaxis_title = 'Frequency', legend_title_text = 'Climate Category', showlegend = True)
fig2.show()

In [6]:
fig1 = px.histogram(raw_data['POSTAL.CODE_'], title='Distribution of Observations by State Code', histnorm = 'probability density')
fig1.update_layout(xaxis = {'categoryorder': 'total descending'})
fig1.show()

In [7]:
raw_data

OBS_   YEAR_  MONTH_   U.S._STATE_ POSTAL.CODE_ NERC.REGION_  \
1        1.0  2011.0     7.0     Minnesota           MN          MRO   
2        2.0  2014.0     5.0     Minnesota           MN          MRO   
3        3.0  2010.0    10.0     Minnesota           MN          MRO   
...      ...     ...     ...           ...          ...          ...   
1532  1532.0  2009.0     8.0  South Dakota           SD          RFC   
1533  1533.0  2009.0     8.0  South Dakota           SD          MRO   
1534  1534.0  2000.0     NaN        Alaska           AK         ASCC   

         CLIMATE.REGION_ ANOMALY.LEVEL_numeric CLIMATE.CATEGORY_  \
1     East North Central                  -0.3            normal   
2     East North Central                  -0.1            normal   
3     East North Central                  -1.5              cold   
...                  ...                   ...               ...   
1532  West North Central                   0.5              warm   
1533  West North Central                   0.5              warm   
1534                 NaN                   NaN               NaN   

     OUTAGE.START.DATE_Day of the week, Month Day, Year  \
1                                   2011-07-01 00:00:00   
2                                   2014-05-11 00:00:00   
3                                   2010-10-26 00:00:00   
...                                                 ...   
1532                                2009-08-29 00:00:00   
1533                                2009-08-29 00:00:00   
1534                                                NaN   

     OUTAGE.START.TIME_Hour:Minute:Second (AM / PM)  \
1                                          17:00:00   
2                                          18:38:00   
3                                          20:00:00   
...                                             ...   
1532                                       22:54:00   
1533                                       11:00:00   
1534                                            NaN   

     OUTAGE.RESTORATION.DATE_Day of the week, Month Day, Year  \
1                                   2011-07-03 00:00:00         
2                                   2014-05-11 00:00:00         
3                                   2010-10-28 00:00:00         
...                                                 ...         
1532                                2009-08-29 00:00:00         
1533                                2009-08-29 00:00:00         
1534                                                NaN         

     OUTAGE.RESTORATION.TIME_Hour:Minute:Second (AM / PM)     CAUSE.CATEGORY_  \
1                                              20:00:00        severe weather   
2                                              18:39:00    intentional attack   
3                                              22:00:00        severe weather   
...                                                 ...                   ...   
1532                                           23:53:00             islanding   
1533                                           14:01:00             islanding   
1534                                                NaN     equipment failure   

     CAUSE.CATEGORY.DETAIL_ HURRICANE.NAMES_ OUTAGE.DURATION_mins  \
1                       NaN              NaN                 3060   
2                 vandalism              NaN                    1   
3                heavy wind              NaN                 3000   
...                     ...              ...                  ...   
1532                    NaN              NaN                   59   
1533                    NaN              NaN                  181   
1534                failure              NaN                  NaN   

     DEMAND.LOSS.MW_Megawatt  CUSTOMERS.AFFECTED_  \
1                        NaN              70000.0   
2                        NaN                  NaN   
3                        NaN              70000.0   
...                      ...         

## Step 3: Assessment of Missingness

### Part 3.1: Missingness Mechanism Analysis
If we look at our feature of interest, we can see that approximately 30 percent of values are missing. This is most likely not MCAR and requires more analysis to see if its missingness depends on other features.

In [8]:
raw_data[['CAUSE.CATEGORY.DETAIL_']]

CAUSE.CATEGORY.DETAIL_
1                       NaN
2                 vandalism
3                heavy wind
...                     ...
1532                    NaN
1533                    NaN
1534                failure

[1534 rows x 1 columns]

In [9]:
raw_data['CAUSE.CATEGORY.DETAIL_'].isna().mean()

np.float64(0.3070404172099087)

In [10]:
raw_data[['CAUSE.CATEGORY.DETAIL_', 'CAUSE.CATEGORY_']]

CAUSE.CATEGORY.DETAIL_     CAUSE.CATEGORY_
1                       NaN      severe weather
2                 vandalism  intentional attack
3                heavy wind      severe weather
...                     ...                 ...
1532                    NaN           islanding
1533                    NaN           islanding
1534                failure   equipment failure

[1534 rows x 2 columns]

In [11]:
''' This cell defines valid, relevant test statistics for permutation and 
hypothesis tests.
'''
def tvd(dist1: pd.Series, dist2: pd.Series):
    return (dist1.value_counts(normalize = True) - dist2.value_counts(normalize = True)).abs().sum() / 2

def ks(dist1: pd.Series, dist2: pd.Series):
    return scipy.stats.ks_2samp(dist1, dist2)

In [46]:
''' This function takes in a dataframe, a column with missing values and a 
column to analyze the type of missingness mechanism with. It will return
a p-value and an associative True or False indicating if missing_col is MAR 
withrespect to col. To conduct the permutation test, it will use the given 
test_stat.

The function will also graph the distribution of simulated test statistics 
with a line indicating where the observed lies.
'''
    
def identify_mar(df, missing_col, col, test_stat, N, alpha):
    missing_dist = df[[col]].assign(is_missing = df[missing_col].isna())
    observed = test_stat(missing_dist[missing_dist['is_missing']][col], missing_dist[~missing_dist['is_missing']][col])
    simulations = np.array([])
    for _ in range(N):
        missing_dist['is_missing'] = np.random.permutation(missing_dist['is_missing'])
        simulated = test_stat(missing_dist[missing_dist['is_missing']][col], missing_dist[~missing_dist['is_missing']][col])
        simulations = np.append(simulations, simulated)
    
    fig = px.histogram(x = simulations, title = f'Permutation Test Distribution', labels={'x': 'Simulated Test Statistics'}, histnorm = 'probability')
    fig.add_vline(x = observed)
    fig.show()    
    
    p_value = (simulations > observed).mean()
    return p_value, p_value < alpha

In [47]:
p_val, is_mar = identify_mar(raw_data, 'CAUSE.CATEGORY.DETAIL_', 'CAUSE.CATEGORY_', tvd, 1000, 0.05)

In [ ]:
p_val2, is_mar2 = identify_mar(raw_data, 'CAUSE.CATEGORY.DETAIL_', 'CLIMATE.CATEGORY_', tvd, 1000, 0.05)
p_val2, is_mar2

(np.float64(0.001), np.True_)

Clearly, the `CAUSE.CATEGORY.DETAIL_` column is **MAR** with respect to `CAUSE.CATEGORY_`. In other words, the missingness for cause category details are *highly* dependent on what the actual cause category is, which makes a lot of sense intuitively.

Now, we will repeat this process for all columns of interest in `raw_data`. We will create a dictionary mapping column names to whether or not they are **MAR** with respect to `CAUSE.CATEGORY.DETAIL_`. Based on this distribution, the next step will be to impute accordingly.

### Part 3.2: Imputation

## Step 4: Hypothesis Testing

$H_0$: The proportion of each cause category is uniformly distributed across each season, for each cause category.

$H_a$: The proportion of each cause category is not uniformly distributed across each season, for each cause category.

In [15]:
seasons = {'(0, 1]': 'Winter', '(1, 4]': 'Spring', '(4, 7]': 'Summer', '(7, 10]': 'Fall', '(10, 12]': 'Winter'}

data = raw_data.copy()
data['SEASONAL.BINS_'] = pd.cut(data['MONTH_'], bins = [0, 1, 4, 7, 10, 12])
data['SEASONAL.BINS_'] = data['SEASONAL.BINS_'].astype(str).map(seasons)
data

OBS_   YEAR_  MONTH_   U.S._STATE_ POSTAL.CODE_ NERC.REGION_  \
1        1.0  2011.0     7.0     Minnesota           MN          MRO   
2        2.0  2014.0     5.0     Minnesota           MN          MRO   
3        3.0  2010.0    10.0     Minnesota           MN          MRO   
...      ...     ...     ...           ...          ...          ...   
1532  1532.0  2009.0     8.0  South Dakota           SD          RFC   
1533  1533.0  2009.0     8.0  South Dakota           SD          MRO   
1534  1534.0  2000.0     NaN        Alaska           AK         ASCC   

         CLIMATE.REGION_ ANOMALY.LEVEL_numeric CLIMATE.CATEGORY_  \
1     East North Central                  -0.3            normal   
2     East North Central                  -0.1            normal   
3     East North Central                  -1.5              cold   
...                  ...                   ...               ...   
1532  West North Central                   0.5              warm   
1533  West North Central                   0.5              warm   
1534                 NaN                   NaN               NaN   

     OUTAGE.START.DATE_Day of the week, Month Day, Year  \
1                                   2011-07-01 00:00:00   
2                                   2014-05-11 00:00:00   
3                                   2010-10-26 00:00:00   
...                                                 ...   
1532                                2009-08-29 00:00:00   
1533                                2009-08-29 00:00:00   
1534                                                NaN   

     OUTAGE.START.TIME_Hour:Minute:Second (AM / PM)  \
1                                          17:00:00   
2                                          18:38:00   
3                                          20:00:00   
...                                             ...   
1532                                       22:54:00   
1533                                       11:00:00   
1534                                            NaN   

     OUTAGE.RESTORATION.DATE_Day of the week, Month Day, Year  \
1                                   2011-07-03 00:00:00         
2                                   2014-05-11 00:00:00         
3                                   2010-10-28 00:00:00         
...                                                 ...         
1532                                2009-08-29 00:00:00         
1533                                2009-08-29 00:00:00         
1534                                                NaN         

     OUTAGE.RESTORATION.TIME_Hour:Minute:Second (AM / PM)     CAUSE.CATEGORY_  \
1                                              20:00:00        severe weather   
2                                              18:39:00    intentional attack   
3                                              22:00:00        severe weather   
...                                                 ...                   ...   
1532                                           23:53:00             islanding   
1533                                           14:01:00             islanding   
1534                                                NaN     equipment failure   

     CAUSE.CATEGORY.DETAIL_ HURRICANE.NAMES_ OUTAGE.DURATION_mins  \
1                       NaN              NaN                 3060   
2                 vandalism              NaN                    1   
3                heavy wind              NaN                 3000   
...                     ...              ...                  ...   
1532                    NaN              NaN                   59   
1533                    NaN              NaN                  181   
1534                failure              NaN                  NaN   

     DEMAND.LOSS.MW_Megawatt  CUSTOMERS.AFFECTED_  \
1                        NaN              70000.0   
2                        NaN                  NaN   
3                        NaN              70000.0   
...                      ...         

In [16]:
''' Calculates the TVD for 2D distributions across each column (axis = 0). 
The resulting TVD's will be aggregated (sum or mean) to represent the TVD of 
the whole distributions. Assumes the probability distributions are already
calculated and provided.
'''
def tvd_2d(dist1: pd.DataFrame, dist2: pd.DataFrame, aggfunc):
    return (np.sum(np.abs(dist1 - dist2), axis = 0) / 2).agg(aggfunc)

In [17]:
seasonal_counts = data.pivot_table(values = 'OBS_', columns = 'SEASONAL.BINS_', index = 'CAUSE.CATEGORY_', aggfunc = 'size')

cause_totals = seasonal_counts.sum(axis = 0)
seasonal_totals = seasonal_counts.sum(axis = 1)
expected_proportions = seasonal_totals / seasonal_counts.sum().sum()

observed_dist = seasonal_counts / cause_totals
expected_dist = pd.DataFrame(data = {col: expected_proportions for col in observed_dist.columns})
observed_tvd = tvd_2d(expected_dist, observed_dist, 'sum')
observed_dist

SEASONAL.BINS_                 Fall  Spring  Summer  Winter
CAUSE.CATEGORY_                                            
equipment failure              0.02    0.04    0.05    0.03
fuel supply emergency          0.02    0.05    0.03    0.03
intentional attack             0.23    0.36    0.23    0.31
islanding                      0.03    0.03    0.04    0.02
public appeal                  0.06    0.02    0.07    0.02
severe weather                 0.57    0.39    0.50    0.53
system operability disruption  0.07    0.11    0.09    0.06

In [18]:
NUM_SIMULATIONS = 1000
sim_season_df = data[['SEASONAL.BINS_', 'CAUSE.CATEGORY_', 'OBS_']]
simulations = []
for _ in range(NUM_SIMULATIONS):
    sim_season_df['SEASONAL.BINS_'] = np.random.permutation(sim_season_df['SEASONAL.BINS_'])
    sim_counts = sim_season_df.pivot_table(values = 'OBS_', columns = 'SEASONAL.BINS_', index = 'CAUSE.CATEGORY_', aggfunc = 'size')

    sim_cause_totals = sim_counts.sum(axis = 0)
    sim_seasonal_totals = sim_counts.sum(axis = 1)
    sim_expected_proportions = sim_seasonal_totals / sim_counts.sum().sum()

    sim_observed_dist = sim_counts / sim_cause_totals
    sim_expected_dist = pd.DataFrame(data = {col: sim_expected_proportions for col in sim_observed_dist.columns})
    sim_tvd = tvd_2d(sim_expected_dist, sim_observed_dist, 'sum')
    
    simulations.append(sim_tvd)
simulations

[np.float64(0.10541337222849258),
 np.float64(0.12726115920737163),
 np.float64(0.11480484477617398),
 np.float64(0.14320546556399666),
 np.float64(0.21230408698275),
 np.float64(0.11642211674558395),
 np.float64(0.1388372054325594),
 np.float64(0.16146291557644893),
 np.float64(0.15177867138260076),
 np.float64(0.1419439265006841),
 np.float64(0.19582425872221168),
 np.float64(0.16731130661106047),
 np.float64(0.13567165175349308),
 np.float64(0.12631439114896878),
 np.float64(0.18509633922778507),
 np.float64(0.15750368081946697),
 np.float64(0.11014955673594176),
 np.float64(0.15294685980089073),
 np.float64(0.1569174636883407),
 np.float64(0.126209051940416),
 np.float64(0.15686004790642913),
 np.float64(0.10837534786597317),
 np.float64(0.16734490019241702),
 np.float64(0.19396071497394057),
 np.float64(0.18928201093820832),
 np.float64(0.10068602153563976),
 np.float64(0.1376085725430221),
 np.float64(0.12816172749698168),
 np.float64(0.14511268324262527),
 np.float64(0.100399966

In [19]:
fig_hyp1 = px.histogram(simulations, histnorm = 'probability', title = 'Cause Category by Season Distribution of TVD')
fig_hyp1.add_vline(x = observed_tvd)
fig_hyp1.show()

In [20]:
p_val_hyp1 = (observed_tvd < simulations).mean()
p_val_hyp1
np.array(simulations).mean(), np.array(simulations).std()

(np.float64(0.14335848945935725), np.float64(0.029666053238096516))

### Test Number 2

$H_0$: The distributions of mean affected customers for each state is the same for observations from 2000-2008 and 2008-2016.

$H_a$: The distributions of mean affected customers for each state is different for observations from 2000-2008 and 2008-2016.

In [42]:
data['YEAR_'] = data['YEAR_'].astype(float)
customers_dist_2008 = data[data['YEAR_'] <= 2008.0][['U.S._STATE_', 'CUSTOMERS.AFFECTED_']].groupby('U.S._STATE_').mean()
customers_dist_2008 /= customers_dist_2008.sum(axis = 0)
customers_dist_2008 = customers_dist_2008['CUSTOMERS.AFFECTED_'].dropna()

customers_dist_2016 = data[data['YEAR_'] > 2008.0][['U.S._STATE_', 'CUSTOMERS.AFFECTED_']].groupby('U.S._STATE_').mean()
customers_dist_2016 /= customers_dist_2016.sum(axis = 0)
customers_dist_2016 = customers_dist_2016['CUSTOMERS.AFFECTED_'].dropna()

observed_tvd_customers = np.abs(customers_dist_2008 - customers_dist_2016).sum() / 2
observed_tvd_customers


np.float64(0.36851805695787)

In [43]:
N_CUSTOMERS = 1000
sim_customers_2016 = np.random.multinomial(N_CUSTOMERS, pvals = customers_dist_2008, size = 100_000) / N_CUSTOMERS
sim_tvds_customers = np.sum(np.abs(sim_customers_2016 - customers_dist_2008.to_numpy()), axis = 1) / 2
px.histogram(sim_tvds_customers).show()
sim_tvds_customers.mean(), sim_tvds_customers.std()

(np.float64(0.07349183247421738), np.float64(0.00943067238695654))

In [45]:
p_val_hyp2 = (np.array(sim_tvds_customers) >= observed_tvd_customers).mean()
p_val_hyp2

np.float64(0.0)

## Step 5: Framing a Prediction Problem

## Step 6: Baseline Model

In [ ]:
# TODO

## Step 7: Final Model

In [ ]:
# TODO

## Step 8: Fairness Analysis

In [ ]:
# TODO